# Explore Kentucky Lidar Data verson deux

![UKy's central campus in lidar point cloud](https://nyc3.digitaloceanspaces.com/astoria/geo409/images/lidar-banner.jpg)     
*UKy's central campus in lidar point cloud*


This notebook will create a LAS dataset from a folder of LAZ files. It will also colorize the point cloud from an RGB image from the ImageServices service hosted on the KyRaster.Ky.gov ArcGIS Server and create raster derivatives for 3D visualizations. Please follow the steps in our lesson  [readme.md](../README.md#application-exploring-kentucky-in-3d) before using this notebook.

In [ ]:
############### Modules and Functions :: DO NOT EDIT ###############

# Import ArcGIS package
import arcpy
# Subprocess allows us to issue commands on the command line
import subprocess
# Zip utlity to extract files
from zipfile import ZipFile
# Get current local time
import datetime

# Allow overwriting of existing data
arcpy.env.overwriteOutput = True

############### Utility functions ###############

def setWork():
    """Create dictionary of path names from global variables 
    and return dot.notation access to dictionary attributes.
    Used internally for shorthand access to path names."""
    class dotdict(dict):
        """dot.notation"""
        __getattr__ = dict.get
        __setattr__ = dict.__setitem__
        __delattr__ = dict.__delitem__
    p = {
        "project": f'{root}\\{folder}',
        "db": f'{root}\\{folder}\\{folder}.gdb',
        "lidar": f'{root}\\{folder}\\lidar',
        "download": f'{root}\\{folder}\\download',
        "laz": f"{root}\\tools\\LAStools\\bin\\laszip64.exe",
        "lasmerge": f"{root}\\tools\\LAStools\\bin\\lasmerge64.exe",
        "grid":  f"{root}\\tools\\grids\\tile-grids.gdb\\KY_5k_LAZ",
        "lasd": f'{root}\\{folder}\\download\\combined.lasd',
        "lasdaoi": f'{root}\\{folder}\\download\\aoi_extract.lasd',
        "lasdaoim": f'{root}\\{folder}\\download\\aoi_merged.lasd',
        "merge": f'{root}\\{folder}\\download\\merged.las',
        "aoi": f'{root}\\{folder}\\download\\aoi.lasd',
        "bands": 'RED Band_1; GREEN Band_2; BLUE Band_3',
        "img": "ImageServices\\Ky_NAIP_2020_2ft",
        "dsm": f'{root}\\{folder}\\lidar\\dsm.lasd',
        "output": 'aoi',
        "name": folder,
        "potree": f"{root}\\tools\\potree\\PotreeConverter.exe",
        "potree2": f"{root}\\tools\\potree2\\PotreeConverter.exe"
        
    }
    return dotdict(p)

def listContents(root, folder):
    """Function to print contents of a directory and report time when the cell finished processing.
    listContents(root, folder)
    Two arguments:
        root = drive letter and folder for your root GIS space (string)
        folder = path to folder in root (string)
    """
    downloads = f'{root}\\{folder}'
    completed = subprocess.run(f'dir {downloads}', shell=True, stdout=subprocess.PIPE)
    print(completed.stdout.decode('UTF-8'))
    print("Finished processing", datetime.datetime.now())

def checkFolder(name):
    """Function to check folder name against special characters for creating project space.
    checkFolder(name)
    One argument:
        name = name of project folder for this application (string)
    """
    special = "\"\' :;\\.!@#$%^&*()-+?=,<>/"
    if any(letter in special for letter in name):
        print("Whoops! You have a special character in your project's name. \nPlease change project name.")
        return False
    else:
        print(f'Checking project folder...')
        return True
    
############### Project Functions :: DO NOT EDIT ###############

def setUpProject():
    """Function to create project folder and database in root GIS.
    setUpProject()
    No arguments
    """
    p = setWork()
    if checkFolder(folder):
        subprocess.run(f'mkdir {p.project}', shell=True)
        subprocess.run(f'mkdir {p.download}', shell=True)
        subprocess.run(f'mkdir {p.lidar}', shell=True)
        print(f'Your project is in the {p.project} folder')
    # Create project geodatabase
    try:
        test_workspace = arcpy.Describe(p.db)
        if test_workspace.dataType == 'Workspace':
            print(f"Output database already exists: {p.db}")
    except:
        arcpy.management.CreateFileGDB(p.project, folder)
        print(f"Created output database: {p.db}")   
    arcpy.env.workspace = p.db
    print(f"Using {arcpy.env.workspace} for output")
#     if arcpy.Exists(p.db):
#         print(f'{p.db} exists!')
#     else:
#         print(f"Creating {p.db}")
#         arcpy.CreateFileGDB_management(p.project, folder)
#     arcpy.env.workspace = p.db
            
def setAoi():
    """Function to create area of interest and clip LAZ grid layer 
    to interactively download LAZ files. The function creates a layer called 'aoi'.
    setAoi()
    The four global variables that it uses:
        lat = latitude for center of AOI (number)
        lon = longitude for center of AOI (number)
        buffer = distance, in feet, from center of AOI to include in analysis (number)
        square {optional} = square (default) or circular aoi polygon
    """
    p = setWork()
    arcpy.env.workspace = p.db
    arcpy.env.extent = 'MAXOF'
    output = f'{p.name}_{p.output}'
    arcpy.env.addOutputsToMap = False
    if custom_aoi:
        arcpy.management.CopyFeatures(custom_aoi, output)
    else:
        out1 = f'_pt_temp'
        out2 = f'_ro_temp'
        wgs84 = arcpy.SpatialReference(4326)
        point = arcpy.Point(lon, lat) 
        ptGeometry = arcpy.PointGeometry(point, wgs84)
        arcpy.management.CopyFeatures(ptGeometry, out1)
        if square:
            arcpy.analysis.Buffer(out1, out2, buffer)
            arcpy.management.FeatureEnvelopeToPolygon(out2, output)
            arcpy.management.Delete(out2)
        else:
            arcpy.analysis.Buffer(out1, output, buffer)
        arcpy.management.Delete(out1)
    arcpy.env.addOutputsToMap = True
    arcpy.analysis.Clip(p.grid, output, f"{output}_laz_grid")
    arcpy.env.extent = output
    print(f"Using {output} for AOI")
    
    
def processLaz(merge = True):
    """Function to convert LAZ file in downloads folder to a LAS dataset and extract AOI point cloud.
    processLaz(aoi)
    One argument:
        merge = True. Will by default combine las files into single file.
    Note: This functions produce duplicate LAS for the AOI dataset. 
    """
    p = setWork()
    aoi = f'{p.name}_{p.output}'
    ky = arcpy.SpatialReference(3089)
    arcpy.env.workspace = p.db
    las_tools = p.laz
    las = []
    subprocess.run(f'dir {p.download}\\*.laz /b > {p.download}\\zips.txt', shell=True, stdout=subprocess.PIPE)
    with open(f'{p.download}\\zips.txt', 'r') as fileList:
        for line in fileList:
            name = line.strip()
            print(f"{las_tools} -i {p.download}\\{name} -o {p.download}\\{name[:-4]}.las")
            subprocess.run(f'{las_tools} -i {p.download}\\{name} -o {p.download}\\{name[:-4]}.las', shell=True, stdout=subprocess.PIPE)
            las.append(f'{p.download}\\{name[:-4]}.las')
    arcpy.env.addOutputsToMap = False
    print(f"Extacting to {p.output}: {p.lasdaoi}")
    arcpy.CreateLasDataset_management (las, p.lasd, "#", "#", ky, True, True)
    if (merge):
        arcpy.ExtractLas_3d (p.lasd, p.download, "#", aoi,  "#", "_e", "#", "#", True, p.lasdaoi)
        print('Command line command that will be executed:')
        print(f'dir {p.download}\\"*_e.las" /b /s > {p.download}\\las.txt')
        completed = subprocess.run(f'dir {p.download}\\"*_e.las" /b /s > {p.download}\\las.txt', shell=True, stdout=subprocess.PIPE)
        print('Command line command that will be executed:')
        print(f"{p.lasmerge} -lof {p.download}\\las.txt -o {p.merge}")
        subprocess.run(f"{p.lasmerge} -lof {p.download}\\las.txt -o {p.merge}")
        arcpy.CreateLasDataset_management (p.merge, p.lasdaoim, "#", "#", ky, True, True)
    else:
        arcpy.ExtractLas_3d (p.lasd, p.download, "#", aoi,  "#", "_e", "#", "#", True, p.lasdaoi)
    arcpy.env.addOutputsToMap = True

        
# Function to unzip downloaded files  
def colorizeWith(image):
    """Function to add color attributes to LAS files from ImageServices RGB image.
    colorizeWith(image)
    One argument:
    image = name of KyRaster ImageServices RGB layer you want use to colorize point cloud (string)
    """
    p = setWork()
    # select = input(f"Do you have the ImagesServices layer {image} loaded? Yes or No ")
    select = 'y'
    aoi = f'{p.name}_{p.output}'
    arcpy.env.addOutputsToMap = False
    if 'y' in select.lower():
        ky = arcpy.SpatialReference(3089)
        arcpy.env.workspace = p.db
        print(f'Colorizing point cloud with {image}')
        aoi = f'{p.name}_{p.output}'
        arcpy.Clip_management(f"{image}", "#", f"{p.name}_img", aoi, "#", "ClippingGeometry")
        arcpy.env.addOutputsToMap = True
        arcpy.ColorizeLas_3d (p.merge, f'{p.name}_img', p.bands, p.lidar, f"_{p.name}_img", "#", "#","#", "#", True, f"{p.lidar}\\{p.name}.lasd")
                
# Function to unzip downloaded files  
def shade(classcodes, name, resolution):
    """Function to create raster elevation and shaded relief models from AOI LAS dataset.
    shade(classcodes, name)
    Three arguments:
        classcodes = LAS class codes used to filter input point cloud (list of integers)
        name = name of output layers (string)
        resolution = pixel resolution in feet. Phase 1 no smaller than 5 and Phase 2 no smaller than 2.5 (Number)
    """
    p = setWork()
    arcpy.env.addOutputsToMap = False
    arcpy.MakeLasDatasetLayer_management (f"{p.lidar}\\{p.name}.lasd", p.dsm, classcodes)
    arcpy.env.addOutputsToMap = True
    arcpy.LasDatasetToRaster_conversion (p.dsm,  f'{p.name}_{name}', "#", "#", "#", "#", resolution)
    arcpy.HillShade_3d(f'{p.name}_{name}', f'{p.name}_{name}_hillshade', 270, 55)
    
# Function to delete temp layers       
def cleanUp():
    """Delete all LAS and LASD files in download folder EXCEPT the merged point cloud and LAZ files.
    cleanUp()
    No arguments
    Note: Make sure final aoi LAS files are saved in the lidar folder. LAZ files are not deleted. 
    """
    select = input(f"Do you want to delete LAS files in downloads folder? Yes or No ")
    p = setWork()
    if 'y' in select.lower():
        subprocess.run(f'dir {p.download}\\*.las* /b /s > {p.download}\\del.txt', shell=True)
        with open(f'{p.download}\\del.txt', 'r') as fileList:
            for line in fileList:
                if 'merged.las' not in line:
                    print(f'Deleting {line}')
                    subprocess.run(f'del {line.strip()}', shell=True)
        print(f'All gone!')
        
def makeViewer(version = 1):
    """Function run command line tool PotreeConverter to create web browser point cloud viewer.
    makeViewer()
    one argument:
        version = 1 or 2. Potree version to use. Version 1 can be uploaded to GitHub Pages. 
                  Version 2 is better, but cannot be hosted on GitHub Pages. (Number)
    """
    p = setWork()
    print('Command line command that will be executed:')
    if (version == 1):
        subprocess.run(f'mkdir {p.project}\\viewer', shell=True)
        print(f"{p.potree} {p.lidar}\\merged_{p.name}_img.las -o {p.project}\\viewer --generate-page index")
        subprocess.run(f"{p.potree} {p.lidar}\\merged_{p.name}_img.las -o {p.project}\\viewer --generate-page index")
    else:
        subprocess.run(f'mkdir {p.project}\\viewer2', shell=True)
        print(f"{p.potree2}  -i {p.lidar}\\merged_{p.name}_img.las -o {p.project}\\viewer2 --generate-page index")
        subprocess.run(f"{p.potree2}  -i {p.lidar}\\merged_{p.name}_img.las -o {p.project}\\viewer2 --generate-page index")
        
# Function to delete downloads folder       
def nuclearBombCleanUp():
    """Delete entire downloads folder.
    nuclearBombcleanUp()
    No arguments and no complaints. 
    Note: Make sure final aoi LAS files are saved in the lidar folder. 
    """
    select = input(f"Do you want to delete the downloads folder? Yes or No ")
    p = setWork()
    if 'y' in select.lower():
        completed = subprocess.run(f'dir {p.lidar}', shell=True, stdout=subprocess.PIPE)
        print(completed.stdout.decode('UTF-8'))
        q = input(f"Do you have a {p.lidar}\\{p.name}.lasd and {p.lidar}\\merged_{p.name}_img.las? ")
        if 'y' in q.lower(): 
            # Delete temporary downloads folder
            command = f'rmdir /Q /S {p.download}'
            print(command)
            completed = subprocess.run(command, shell=True, stdout=subprocess.PIPE)
            print(completed.stdout.decode('UTF-8'))
        print(f'All gone!')



## Before you start
* Either run the *downloads.ipynb* to set up your environment, or download and extract [tools](https://nyc3.digitaloceanspaces.com/astoria/geo409/start/tools.zip) folder into your root GIS space.
* Create a new Map Project in your root GIS folder.


In [ ]:
############### Global variables :: EDIT for your AOI ###############

# Directory path to your root GIS folder. 
root = "c:\\BoydsGIS"

# Project name - creates a folder in your root GIS directory.
# Use only letters and underscores, no numbers, spaces, etc.
folder = "FortKnox"

# Custom AOI location on disk. Leave empty if you want to create an AOI from a point location.
# Example of an empty string
custom_aoi = ''
# custom_aoi = 'c:/BoydsGIS/data/campus.gdb/boundary' # Example using campus as AOI

# AOI from a point. Only works when custom_aoi = ''
# Where is your Area of Interest in Kentucky?
lat = 37.883233978202185
lon = -85.96533786499123

# How far in feet from the above point do you want to process lidar data?
# Increasing this distance exponetially increases file sizes
buffer = 1000

# Square or circular area of interest
square = True

# Set coordinate system to Kentucky
ky = arcpy.SpatialReference(3089)
arcpy.env.outputCoordinateSystem = ky

In [ ]:
# Create folder and database to store project
setUpProject()

In [ ]:
# Set or create AOI
setAoi()

In [ ]:
# Check if laz grid is in database
features = arcpy.ListFeatureClasses()
print(features)

## Download LAZ files

Instructions

1. Verify a new layer called *laz_grid* is in your content pane. If not, add it to your scene from the project's geodatabase.
2. Click on each tile in the layer. Click on *download_url* and save them to your project's *download* folder.
3. Make note of the year that the lidar was scanned. This will be used to match the best aerial imagery to use for colorizing.


![Download LAZ files for your area of interest](https://nyc3.digitaloceanspaces.com/astoria/geo409/images/add-grid.jpg)    
*Download LAZ files for your area of interest*

4. After downloading all of the LAZ files, move them to your project's *download* folder.

In [ ]:
# Let's see if you LAZ files in your project's download folder
listContents(root, f'{folder}\\download')

In [ ]:
# Decompress the LAZ files and merge into a single LAS file.
processLaz()

In [ ]:
# What image are you using to colorize the point cloud?
# For best results, chose a time that matches the lidar year.
image = r'https://kyraster.ky.gov/arcgis/rest/services/ImageServices/Ky_NAIP_2022_2FT/ImageServer'

# Colorize the point cloud
colorizeWith(image)

In [ ]:
# Let's see if you have a merged LAS for upload to online 3D mapping platforms
listContents(root, f'{folder}\\lidar')
print(f"Do you see: merged_{folder}_img.las? That's the colorized merged file you can use.")

## Create a raster surface model from LAS dataset

Access the dataset's **Properties > LAS Filter** dialog to see which classification codes exist. For bare-earth DEM, use only `2`. For above-ground features, use `1` and `2`. Some areas in Kentucky might have additional classification codes.

![Access LAS properties](https://nyc3.digitaloceanspaces.com/astoria/geo409/images/lasd-props.jpg)    
*Accessing LAS properties*

In [ ]:
# What is the name of the raster elevation model you will create?
elevName = 'dem_2019_2ft'

# Default class codes for ground and above-ground features.
ground = [2]
above = [1, 2, 9, 17, 20]

# Pixel resolution in feet. Phase 1 should be no smaller than 5 and Phase 2 no smaller than 2.5 
resolution = 2

shade(ground, elevName, resolution) # bare-earth DEM

In [ ]:
rasters = arcpy.ListRasters()
print(rasters)

## Custom colorizing technique for point clouds

Use the hillshade function to simulate the sun on the horizon cast shadows on the DSM. After creating the hillshade, export the layer as RGB raster by right-clicking the raster layer in the **Contents Pane > Data > Export Raster** and enable **RGB** out and **Force RGB**. Finally, colorize the point cloud.

In [ ]:
# Discover rasters in geodatabase
rasters = arcpy.ListRasters()
print(rasters)

In [ ]:
# Create hillshade

# Set parameters
inputSurface = 'BigFourP1_dsm_2012'
outputSurface = 'sunrise'
sunAzimuth = 90
sunAltitude = 10
surfaceExaggeration = 2
castShadows = True

# Run function
arcpy.ddd.HillShade(inputSurface, outputSurface, sunAzimuth, sunAltitude, castShadows, surfaceExaggeration)

In [ ]:
# Discover rasters in geodatabase
rasters = arcpy.ListRasters()
print(f'Workspace raster: {rasters}')
print(f'Current project path: {root}\\{folder}')

In [ ]:
# Set parameters to colorize point cloud

# Image to use to colorize las file
inImage = 'sunriseHill'

# Bands in this image
bands = 'RED Band_1; GREEN Band_2; BLUE Band_3'

# point cloud to colorize
inCloud = f'{root}\\{folder}\\lidar\\{folder}.lasd'

# output point cloud
outCloud = f'{root}\\{folder}\\lidar\\{folder}_sunColored.lasd'

# out folder to store colorized las files
outFolder = f'{root}\\{folder}\\lidar\\sun'

# Make folder for colorized las files
subprocess.run(f'mkdir {outFolder}', shell=True, stdout=subprocess.PIPE)

In [ ]:
# Colorize point cloud
arcpy.ddd.ColorizeLas(inCloud, inImage, bands, outFolder, "_sunColored","#", "#", "#", "#", "#", outCloud)

## Comparing DSM change 
After two DSM from different years are loaded, compare change by subtracting the older DSM from the recent DSM.

In [ ]:
# See if earlier DSM is loaded
# Uncomment the below line to load the DSM
dsm_2012 = arcpy.sa.Raster('c:\\BoydsGIS\\BigFourP1\\BigFourP1.gdb\\BigFourP1_dsm_2012')
dsm_2012

In [ ]:
# See if redent DSM is loaded
# Uncomment the below line to load the DSM
dsm_2023 =  arcpy.sa.Raster('c:\\BoydsGIS\\BigFourP2\\BigFourP2.gdb\\BigFourP2_dsm_2023')
dsm_2023

In [ ]:
change_uncleaned = (dsm_2023 - dsm_2012)

In [ ]:
# Smooth surface to remove artifacts along the edges of tall structures
neighborhood = arcpy.sa.NbrRectangle(3, 3, 'CELL')
change = arcpy.sa.FocalStatistics(change_uncleaned, neighborhood , 'MEDIAN')

In [ ]:
# Where has there been vally fill and mountain top removal
filled = arcpy.sa.Con((change > 2), change, 0)
removed = arcpy.sa.Con((change < -2), change, 0)

## Export two rasters
Symbolize each raster and then export as RBG raster by right-clicking the raster layer in the **Contents Pane > Data > Export Raster** and enable **RGB** out and **Force RGB**

In [ ]:
# Edit workspace properties for custom colorized las files

# Set root GIS folder
rootGIS = 'c:\\BoydsGIS'

# Set project name (should be folder name created by this Notebook and the name of the lAS dataset)
projectName = 'BigSandy_2019'

# Analysis name (will create a folder to store output colorized lass files)
analysisName = 'filled'

# Image to use to colorize las file
inImage = 'c:\\BoydsGIS\\BigSandy_2019\\BigSandy_2019.gdb\\filled'

# Bands in this image
bands = 'RED Band_1; GREEN Band_2; BLUE Band_3'

In [ ]:
# Set paths for function. Likely will not have to edit.
inCloud = f'{rootGIS}\\{projectName}\\lidar\\{projectName}.lasd'
lidarFolder = f'{rootGIS}\\{projectName}\\lidar\\{analysisName}'
lasSuffix = f'_{analysisName}'
outCloud =  f'{rootGIS}\\{projectName}\\lidar\\{projectName}_{analysisName}.lasd'

In [ ]:
# Check if files exist...
listContents(rootGIS, f'{projectName}\\lidar\\')
print(f'Do you see {rootGIS}\\{projectName}\\lidar\\{projectName}.lasd ?')

In [ ]:
# Make folder for colorized las files
subprocess.run(f'mkdir {lidarFolder}', shell=True, stdout=subprocess.PIPE)

In [ ]:
# Colorize point cloud
arcpy.ddd.ColorizeLas(inCloud, inImage, bands, lidarFolder, lasSuffix,"#", "#", "#", "#", "#", outCloud)

## Browser viewer for point clouds

The *tools* folder has two PotreeConverter versions. Version 2 is the current version, but it produces files that are too large to be hosted on GitHub Pages. Version 1 is no longer being maintained, but it produces many small files that can be hosted on GitHub Pages.

![Point cloud viewer](https://nyc3.digitaloceanspaces.com/astoria/geo409/images/add-image-potree.jpg)    
*Point cloud viewer*

In [ ]:
# Make a Potree point cloud viewer for the Browser.
makeViewer(version = 1)

## Clean up 

After you have succesfully created a colorized point cloud and it is saved in your *lidar* folder, you can start removing redundant data. You have two options. 

1. `cleanUp()` will remove duplicate las and lasd files in the *downloads* folder. It will NOT delete the uncolorized merged las file nor the LAZ files. You can always quickly rebuild a project with this option.
2. `nuclearBombCleanUp()` will delete the ENTIRE *downloads* folder to minimize the project's disk space. To rerun this Notebook, you will need to download the LAZ files again.

In [ ]:
# FYI: look at the contents of lidar folder
listContents(root, f'{folder}\\lidar')

In [ ]:
# Remove duplicate LAS and LASD files
cleanUp()

In [ ]:
help(nuclearBombCleanUp)

In [ ]:
# yolo dude
nuclearBombCleanUp()

The end of data processing. Go back to the lesson documentation to create a map layout and 3D animation of your point cloud.